In [ ]:
import numpy as np

import matplotlib
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

from matplotlib import pyplot as plt
import matplotlib.patches as mpatches
#import compute_sigmalm0_SimIMREOBGenerateQNMFreqV2 as calcqnm
from matplotlib.ticker import MultipleLocator,AutoMinorLocator
import h5py

import seaborn as sns
sns.set(style='ticks', context='notebook', palette='colorblind', font='serif')

import utils
plt.rcParams.update(utils.rcParams)
from jinja2 import Template
#import lal
import json


from pesummary.core.plots.bounded_1d_kde import bounded_1d_kde as Bounded_1d_kde

In [ ]:
import pesummary
pesummary.__version__

In [ ]:
# A list of events
event_list = ["GW150914", "GW170104", 'S190519bj','S190521r', "S190630ag", \
              "S190828j", 'S190910s', "S191109d", "S200129m", \
              "S200208q", "S200224ca", "S200311bg"]

mtotal_dict = json.load(open("./dict_det_masses.json"))

# Color for each event
color_dict = dict(zip(event_list, \
                      [sns.color_palette("Set1", desat=0.7)[0] for idx in range(len(event_list))]))

cmap      = plt.cm.coolwarm
#norm      = matplotlib.colors.Normalize(vmin=(55.0), vmax=(160.0));
norm      = matplotlib.colors.TwoSlopeNorm(105.0, vmin=(50.0), vmax=(160.0));

alpha = 0.2

# Prior used for each event
# All the events use a prior on both domega220 and dtau220: [-0.8,2.0] ...
prior_dict = {
    "dtau_220-min": dict(zip(event_list, -0.8*np.ones(len(event_list)))),
    "dtau_220-max": dict(zip(event_list, 2.*np.ones(len(event_list)))),
    "domega_220-min": dict(zip(event_list, -0.8*np.ones(len(event_list)))),
    "domega_220-max": dict(zip(event_list, 2.*np.ones(len(event_list))))
}

# ... except S1901109d and S200208q, which use domega220-max=4, and dtau220-max=4
# So for these two events, use explicitly set the prior:
for event in ["S191109d", "S200208q"]:
    prior_dict["domega_220-max"][event] = 4.0
    prior_dict["dtau_220-max"][event] = 4.0
    
data_file_path_template = "./{event}/rin_{event}_pseobnrv4hm_{param}.dat.gz"

# Parameters to be visualized
params = ["domega_220", "dtau_220"]

In [ ]:
def kde_helper(samples, xlow=None, xhigh=None):
    # Initialize bounded KDE
    if xlow is None:
        xlow = np.amin(samples)
    if xhigh is None:
        xhigh = np.amax(samples)
    kde = Bounded_1d_kde(samples, xlow=xlow, xhigh=xhigh)
    pts = np.linspace(xlow, xhigh, num=500)
    pdf = kde(pts)
    
    return pts, pdf

# Load samples first
sample_dict = {}
for param in params:
    sample_dict[param] = {}
    for event in event_list:
        sample_dict[param][event] = np.loadtxt(data_file_path_template.format(event=event, param=param))

color1 = '#32a6a8'
color2 = '#6132a8'
color3 = '#a87932'

# Tune the min and max params
df_220_min = -0.5
df_220_max = 1.
dtau_220_min = -0.5
dtau_220_max = 1.
tick_pos = np.linspace(df_220_min, df_220_max, num=5)

#fig = plt.figure(dpi=150, figsize=utils.figsize_square) # Make a square plot
fig = plt.figure(figsize=(5,5), dpi=200)
gs = fig.add_gridspec(ncols=2, nrows=2, width_ratios=[7,1], height_ratios=[1,7])
# Tune the plot settings
ax_joint = fig.add_subplot(gs[1,0])
ax_joint.set_xlabel(r"$\delta \hat{f}_{220}$")
ax_joint.set_ylabel(r"$\delta \hat{\tau}_{220}$")
ax_joint.set_xticks(tick_pos)
ax_joint.set_yticks(tick_pos)
linewidth = 1

ax_df_220 = fig.add_subplot(gs[0,0], sharex=ax_joint)
plt.setp(ax_df_220.get_xticklabels(), visible=False)
plt.setp(ax_df_220.get_yticklabels(), visible=False)
ax_dtau_220 = fig.add_subplot(gs[1,1], sharey=ax_joint)
plt.setp(ax_dtau_220.get_xticklabels(), visible=False)
plt.setp(ax_dtau_220.get_yticklabels(), visible=False)
plt.subplots_adjust(hspace=0.,wspace=0.)

for event in event_list:
    #e = utils.Event(event)
    
    c = cmap(norm(mtotal_dict[event]))
    
    # Plot domega220 first
    pts, pdf = kde_helper(sample_dict["domega_220"][event])#, xlow=prior_dict["domega_220-min"][event], xhigh=prior_dict["domega_220-max"][event])
    if event == "GW150914":
        ax_df_220.plot(pts, pdf, linewidth=2.0, color=c, label=event, alpha=0.7)
    elif event == "S200129m":
        ax_df_220.plot(pts, pdf, linewidth=2.0, color=c, label="GW200129\_065458", linestyle='dashdot', alpha=0.7)
    else:
        ax_df_220.plot(pts, pdf, linewidth=linewidth, color=c, alpha=alpha, linestyle='dashdot')
    ax_df_220.axvline(0, ls="--", c="grey", linewidth=linewidth)
    
    # Plot dtau220 next
    pts, pdf = kde_helper(sample_dict["dtau_220"][event], xlow=prior_dict["dtau_220-min"][event], xhigh=prior_dict["dtau_220-max"][event])
    if event == "GW150914":
        ax_dtau_220.plot(pdf, pts, linewidth=2.0, color=c, alpha=1)
    elif event == "S200129m":
        ax_dtau_220.plot(pdf, pts, linewidth=2.0, color=c, linestyle='dashdot', alpha=1)
    else:
        ax_dtau_220.plot(pdf, pts, linewidth=linewidth, color=c, alpha=alpha, linestyle='dashdot')
    ax_dtau_220.axhline(0, ls="--", c="grey", linewidth=linewidth)
    
    # Plot the joint distribution (with 90% contour) at last using utils.kdeplot_2d_clevels
    # We fix the random seed here for consistency
    np.random.seed(190521)
    # Reduce the number of samples used to train the Gaussian KDE for speed
    choice = np.random.choice(len(sample_dict["domega_220"][event]), size=5000)
    x_train = sample_dict["domega_220"][event][choice]
    y_train = sample_dict["dtau_220"][event][choice]
    # The bounded and unbounded 2D KDE look the same. Use bounded_2d_kde anyway
    if event == "GW150914":
        utils.kdeplot_2d_clevels(x_train, y_train, levels=[0.90], xlow=prior_dict["domega_220-min"][event], xhigh=prior_dict["domega_220-max"][event], ylow=prior_dict["dtau_220-min"][event], yhigh=prior_dict["dtau_220-max"][event], ax=ax_joint, linewidths=[2.0], colors=[c], alpha=1)
    elif event == "S200129m":
        utils.kdeplot_2d_clevels(x_train, y_train, levels=[0.90], xlow=prior_dict["domega_220-min"][event], xhigh=prior_dict["domega_220-max"][event], ylow=prior_dict["dtau_220-min"][event], yhigh=prior_dict["dtau_220-max"][event], ax=ax_joint, linewidths=[2.0], colors=[c], alpha=1, linestyles=['dashdot'])
    else:
        utils.kdeplot_2d_clevels(x_train, y_train, levels=[0.90], xlow=prior_dict["domega_220-min"][event], xhigh=prior_dict["domega_220-max"][event], ylow=prior_dict["dtau_220-min"][event], yhigh=prior_dict["dtau_220-max"][event], ax=ax_joint, linewidths=[linewidth], colors=[c], alpha=alpha, linestyles=['dashdot'])
        
ax_joint.axvline(0, ls="--", c="grey", linewidth=linewidth)
ax_joint.axhline(0, ls="--", c="grey", linewidth=linewidth)


# Plot the hierarchical results
domega220_hier = np.loadtxt("./cache/rin/pseob/{param}_pop.txt.gz".format(param="domega_220"))
dtau220_hier = np.loadtxt("./cache/rin/pseob/{param}_pop.txt.gz".format(param="dtau_220"))

# Plot the hierarchical results
# domega_220
df_220_hier_pts, df_220_hier_pdf = kde_helper(domega220_hier)
ax_df_220.plot(df_220_hier_pts, df_220_hier_pdf, linewidth=1.2*linewidth, c="k", ls="-.", label="hierarchically\ncombined")
# dtau_220
dtau_220_hier_pts, dtau_220_hier_pdf = kde_helper(dtau220_hier)
ax_dtau_220.plot(dtau_220_hier_pdf, dtau_220_hier_pts, linewidth=1.2*linewidth, c="k", ls="-.")


# Plot the joint likelihood results
domega220_comb = np.loadtxt("./combined_samples/{param}_comb.dat.gz".format(param="domega_220"))
dtau220_comb = np.loadtxt("./combined_samples/{param}_comb.dat.gz".format(param="dtau_220"))


# domega_220
df_220_comb_pts, df_220_comb_pdf = kde_helper(domega220_comb)
ax_df_220.fill(df_220_comb_pts, df_220_comb_pdf, linewidth=0.7*linewidth, facecolor='k', edgecolor='k', alpha=0.2, label="joint\nposterior")
# dtau_220
dtau_220_comb_pts, dtau_220_comb_pdf = kde_helper(dtau220_comb)
ax_dtau_220.fill(dtau_220_comb_pdf, dtau_220_comb_pts, linewidth=0.7*linewidth, facecolor='k', edgecolor='k', alpha=0.2)

choice = np.random.choice(len(domega220_comb), size=5000)
x_train = domega220_comb[choice]
y_train = dtau220_comb[choice]
utils.kdeplot_2d_clevels(x_train, y_train, levels=[0.90], xlow=prior_dict["domega_220-min"][event], xhigh=prior_dict["domega_220-max"][event], ylow=prior_dict["dtau_220-min"][event], yhigh=prior_dict["dtau_220-max"][event], ax=ax_joint, linewidths=[2.0], colors=['k'], alpha=0.2)
utils.kdeplot_2d_clevels_contourf(x_train, y_train, levels=[0.90,0.01], xlow=prior_dict["domega_220-min"][event], xhigh=prior_dict["domega_220-max"][event], ylow=prior_dict["dtau_220-min"][event], yhigh=prior_dict["dtau_220-max"][event], ax=ax_joint, linewidths=[1.0], colors=['k'], alpha=0.2)



ax_joint.set_xlim(df_220_min, df_220_max)
ax_joint.set_ylim(dtau_220_min, dtau_220_max)
ax_df_220.set_ylim(bottom=0.0)
ax_dtau_220.set_xlim(left=0.0)
ax_df_220.axis("off")
ax_dtau_220.axis("off")

# put on ticks
ax_joint.xaxis.set_minor_locator(AutoMinorLocator())
ax_joint.yaxis.set_minor_locator(AutoMinorLocator())
ax_joint.tick_params(axis="x",which='minor',length=5,bottom=True,left=True,top=True,right=True,direction='in')
ax_joint.tick_params(axis="y",which='minor',length=5,bottom=True,left=True,top=True,right=True,direction='in')
ax_joint.tick_params(axis="x",which='major',length=10,labelsize=15,bottom=True,left=True,top=True,right=True,direction='in')
ax_joint.tick_params(axis="y",which='major',length=10,labelsize=15,bottom=True,left=True,top=True,right=True,direction='in')


ax_joint.legend(*ax_df_220.get_legend_handles_labels(), loc=1, frameon=False,prop={'size': 12})


In [ ]:
def ComputeSymCIedges(samples, ci=0.9):
    """ Symmetric CI.
    """
    lo = np.percentile(samples, 100.0 * (1-ci)*0.5)
    hi = np.percentile(samples, 100.0 * (1-(1-ci)*0.5))
    return hi, lo

# ----------------------------------------------------------------------------
# Summary
# ----------------------------------------------------------------------------


def get_summary(samples, p=0.9):
    ci_dict = {}
    print("Symmetric {}%-credible interval".format(int(p*100)))
    print("--------------------------------")
    ci1, ci2 = ComputeSymCIedges(np.array(samples), p)
    med = np.median(np.array(samples))
    return print('\t%.2f +%.2f -%.2f\t[%.2f]' % (med, ci1-med, med-ci2, ci1-ci2))

In [ ]:
get_summary(domega220_hier)
get_summary(dtau220_hier)

In [ ]:
get_summary(domega220_comb)
get_summary(dtau220_comb)

In [ ]:
get_summary(sample_dict["domega_220"]['GW150914'])
get_summary(sample_dict["dtau_220"]['GW150914'])

In [ ]:
get_summary(sample_dict["domega_220"]['S200129m'])
get_summary(sample_dict["dtau_220"]['S200129m'])

## Plot bounds

In [ ]:
# Set style for plots using O3a TGR settings
sns.set(style='ticks', context='notebook', font='serif', 
        font_scale=1.5, palette='colorblind')
plt.rcParams.update(utils.rcParams)

# further tune some rcParams
plt.rcParams.update({
    'ytick.labelsize': 0.6*utils.fs_label,
    'legend.fontsize': 0.8*utils.fs_label,
})

# Specify some aesthetic colours...
dodgerblue      = '#1E90FF'
lawngreen       = '#7CFC00'
blueviolet      = '#8A2BE2'
caltechorange   = '#FF6C0C'
walesaway       = '#293133'
waleshome       = '#ff0038'
uniwienblue     = '#006699'
uniwiengrey     = '#666666'
emeraldgreen    = '#50C878'
tanzaniagreen   = '#1eb53a'
grey3           = '#565759'
grey1           = '#C0BEC6'
grey2           = '#AAA7B0'

kwargs ={
    'GWTC-3 (Phenom)':{
        'markeredgewidth': 2,
        'markersize': 12,
        'alpha': 0.8,
        'marker': 6,
        'color': '0.6',
        'ls': '',
    },
    'GWTC-3 (SEOB)':{
        'markeredgewidth': 1,
        'markersize': 12,
        'alpha': 0.8,
        'marker': 6,
        'markeredgecolor': 'k',
        'markerfacecolor': 'none',
        'ls': '',
    },
    'GWTC-2 (Phenom)':{
        'markeredgewidth': 2,
        'markersize': 12,
        'alpha': 0.8,
        'marker': 7,
        'color': '0.6',
        'ls': '',
    },
    'GWTC-2 (SEOB)':{
        'markeredgewidth': 1,
        'markersize': 12,
        'alpha': 0.8,
        'marker': 7,
        'markeredgecolor': 'k',
        'markerfacecolor': 'none',
        'ls': '',
    },
    'GWTC-1 (Phenom)':{
        'markeredgewidth': 0.5,
        'markersize': 15,
        'marker': '.',
        'color': waleshome,
        'markeredgecolor': 'w',
        'ls': '',
    },
    'GW170817 (Phenom)': {
        'markeredgewidth': 0.5,
        'markersize': 15,
        'marker': '.',
        'color': dodgerblue,
        'markeredgecolor': 'w',
        'ls': '',
    },
    'event': {
        'marker': '_',
        'ls': '',
        'markersize': 20,
        'alpha': 0.5,
        'markeredgewidth': 3,
    },
    'GW150914': {
        'marker': 'D',
        'ls': '',
        'markersize': 5,
        'alpha': 0.8,
        'markeredgewidth': 2,
        #'markerfacecolor': 'none',
    },
    'S200129m': {
        'marker': 's',
        'ls': '',
        'markersize': 5,
        'alpha': 0.5,
        'markeredgewidth': 2,
        #'markerfacecolor': 'none',
    }
}

In [ ]:
print(f"Event \t Total Mass \t CI:domega220 \t CI:domega220")

fig = plt.figure(figsize=(2,5), dpi=200)
ax = fig.add_subplot(111)

for event in event_list:
    
    domega220_pts, domega220_pdf = kde_helper(sample_dict["domega_220"][event], xlow=prior_dict["domega_220-min"][event], xhigh=prior_dict["domega_220-max"][event])
    dtau220_pts, dtau220_pdf = kde_helper(sample_dict["dtau_220"][event], xlow=prior_dict["dtau_220-min"][event], xhigh=prior_dict["dtau_220-max"][event])
    
    domega220_left, domega220_right = utils.get_sym_interval_from_pdf(domega220_pdf, domega220_pts, p=0.9, normalize=True)
    dtau220_left, dtau220_right = utils.get_sym_interval_from_pdf(dtau220_pdf, dtau220_pts, p=0.9, normalize=True)

    
    c = cmap(norm(mtotal_dict[event]))
    
    print(f"{event} \t {mtotal_dict[event]} \t {domega220_right - domega220_left:.2f} \t {dtau220_right - dtau220_left:.2f}")
    
    if event == 'GW150914':
        ax.semilogy(0, domega220_right - domega220_left, c=c, **kwargs['GW150914'])
        ax.semilogy(1, dtau220_right - dtau220_left, c=c, **kwargs['GW150914'])
    elif event == 'S200129m':
        ax.semilogy(0, domega220_right - domega220_left, c=c, **kwargs['S200129m'])
        ax.semilogy(1, dtau220_right - dtau220_left, c=c, **kwargs['S200129m'])
    else:
        ax.semilogy(0, domega220_right - domega220_left, c=c, **kwargs['event'])
        ax.semilogy(1, dtau220_right - dtau220_left, c=c, **kwargs['event'])


# condifence intervals on combined posteriors    
domega220_comb_left, domega220_comb_right = utils.get_sym_interval_from_pdf(df_220_comb_pdf, df_220_comb_pts, p=0.9, normalize=True)
dtau220_comb_left, dtau220_comb_right = utils.get_sym_interval_from_pdf(dtau_220_comb_pdf, dtau_220_comb_pts, p=0.9, normalize=True)
ax.semilogy(0, domega220_comb_right - domega220_comb_left, **kwargs['GWTC-2 (Phenom)'], label="joint\nlikelihood")
ax.semilogy(1, dtau220_comb_right - dtau220_comb_left, **kwargs['GWTC-2 (Phenom)'])

print(f"Joint lklhd \t -- \t {domega220_comb_right - domega220_comb_left:.2f} \t {dtau220_comb_right - dtau220_comb_left:.2f}")

# condifence intervals on hierarchical posteriors
domega220_hier_left, domega220_hier_right = utils.get_sym_interval_from_pdf(df_220_hier_pdf, df_220_hier_pts, p=0.9, normalize=True)
dtau220_hier_left, dtau220_hier_right = utils.get_sym_interval_from_pdf(dtau_220_hier_pdf, dtau_220_hier_pts, p=0.9, normalize=True)
ax.semilogy(0, domega220_hier_right - domega220_hier_left, **kwargs['GWTC-2 (SEOB)'], label="hierarchically\ncombined" )
ax.semilogy(1, dtau220_hier_right - dtau220_hier_left, **kwargs['GWTC-2 (SEOB)'])
    
print(f"Hier \t -- \t {domega220_hier_right - domega220_hier_left:.2f} \t {dtau220_hier_right - dtau220_hier_left:.2f}")    
 
# O3a TGR paper bounds
# Plot the joint likelihood results
domega220_comb_O3a = np.loadtxt("./combined_samples/{param}_comb_pseobO3a.dat.gz".format(param="domega_220"))
dtau220_comb_O3a = np.loadtxt("./combined_samples/{param}_comb_pseobO3a.dat.gz".format(param="dtau_220"))


# domega_220
df_220_comb_pts_O3a, df_220_comb_pdf_O3a = kde_helper(domega220_comb_O3a)
# dtau_220
dtau_220_comb_pts_O3a, dtau_220_comb_pdf_O3a = kde_helper(dtau220_comb_O3a)

# condifence intervals on combined posteriors    
domega220_comb_left_O3a, domega220_comb_right_O3a = utils.get_sym_interval_from_pdf(df_220_comb_pdf_O3a, df_220_comb_pts_O3a, p=0.9, normalize=True)
dtau220_comb_left_O3a, dtau220_comb_right_O3a = utils.get_sym_interval_from_pdf(dtau_220_comb_pdf_O3a, dtau_220_comb_pts_O3a, p=0.9, normalize=True)
ax.semilogy(0, domega220_comb_right_O3a - domega220_comb_left_O3a, **kwargs['GWTC-3 (Phenom)'], label="joint\nlikelihood")
ax.semilogy(1, dtau220_comb_right_O3a - dtau220_comb_left_O3a, **kwargs['GWTC-3 (Phenom)'])

print(f"Joint lklhd (O3a) \t -- \t {domega220_comb_right_O3a - domega220_comb_left_O3a:.2f} \t {dtau220_comb_right_O3a - dtau220_comb_left_O3a:.2f}")

# condifence intervals on hierarchical posteriors
# Plot the hierarchical results
domega220_hier_O3a = np.loadtxt("./cache/rin/pseobO3a/{param}_pop.txt.gz".format(param="domega_220"))
dtau220_hier_O3a = np.loadtxt("./cache/rin/pseobO3a/{param}_pop.txt.gz".format(param="dtau_220"))

# Plot the hierarchical results
# domega_220
df_220_hier_pts_O3a, df_220_hier_pdf_O3a = kde_helper(domega220_hier_O3a)
# dtau_220
dtau_220_hier_pts_O3a, dtau_220_hier_pdf_O3a = kde_helper(dtau220_hier_O3a)

domega220_hier_left_O3a, domega220_hier_right_O3a = utils.get_sym_interval_from_pdf(df_220_hier_pdf_O3a, df_220_hier_pts_O3a, p=0.9, normalize=True)
dtau220_hier_left_O3a, dtau220_hier_right_O3a = utils.get_sym_interval_from_pdf(dtau_220_hier_pdf_O3a, dtau_220_hier_pts_O3a, p=0.9, normalize=True)
ax.semilogy(0, domega220_hier_right_O3a - domega220_hier_left_O3a, **kwargs['GWTC-3 (SEOB)'], label="hierarchically\ncombined" )
ax.semilogy(1, dtau220_hier_right_O3a - dtau220_hier_left_O3a, **kwargs['GWTC-3 (SEOB)'])
    
print(f"Hier (O3a) \t -- \t {domega220_hier_right_O3a - domega220_hier_left_O3a:.2f} \t {dtau220_hier_right_O3a - dtau220_hier_left_O3a:.2f}")    
 
    
ax.set_xticks(np.arange(len(params)))
ax.set_xticklabels([r"$\delta \hat{f}_{220}$",r"$\delta \hat{\tau}_{220}$"], fontsize=15, rotation=90)
ax.tick_params(axis='y', labelsize=16)
ax.set_ylabel("$|\delta \hat{\sigma}_i|$")
# grid 
ax.grid(which='major',axis='both', b=True, linestyle='-',alpha=0.6)
ax.grid(which='minor',b=True, linestyle='-',alpha=0.2)    

# Set x- and y-limits    
ax.set_xlim(-1.0, 2.0)

# add colorbar
sm   = plt.cm.ScalarMappable(cmap=cmap, norm=norm)
sm.set_array([])
cbar = plt.colorbar(sm, ticks=np.linspace(55, 165, 12))
cbar.ax.set_yticklabels(cbar.ax.get_yticklabels(), fontsize=12)
cbar.ax.tick_params('y', length=3, which='major')
cbar.set_label(r'$ (1 + z) M / M_{\odot}$', fontsize=18, labelpad=2.5)


## Table with reconstructed values

In [ ]:
import json

In [ ]:
# using fitting formulas from https://arxiv.org/pdf/gr-qc/0512160.pdf
# to get final mass and final spin from omega220 and tau220.
# See eqs.2.1, E1 and E2, and table VIII for fitting coefficients

G_SI = 6.67430e-11
C_SI = 299792458e0
MSUN_SI = 1.988409902147041637325262574352366540e30

def Mjfinal220(omega220,tau220):

    jf=1-pow((omega220*tau220/2.-0.7)/(1.4187),-1/0.4990)
    Mf=((1.5251 - 1.1568*pow((1 - jf),0.1292))/omega220)*(pow(C_SI,3)/G_SI/MSUN_SI)
    
    idx, = np.where(jf < 0.)
    jf[idx] = 0.
    
    Mf[np.isnan(Mf)] = 0.
    jf[np.isnan(jf)] = 0.

    return Mf,jf

params = ["freq_modGR", "tau_modGR", "Mf", "af"]
sample_dict = {}

for param in params:
    sample_dict[param] = {}

for idx, gid in enumerate(event_list):
    

    freq_modGR = np.loadtxt(f"./{gid}/rin_{gid}_pseobnrv4hm_freq_220_modGR.dat.gz")
    tau_modGR = np.loadtxt(f"./{gid}/rin_{gid}_pseobnrv4hm_tau_220_modGR.dat.gz")
    
    Mf, af = Mjfinal220(2.*np.pi*freq_modGR,tau_modGR)
    
    tau_modGR *= 1.e3
    
    sample_dict["freq_modGR"][gid] = freq_modGR
    sample_dict["tau_modGR"][gid] = tau_modGR
    sample_dict["Mf"][gid] = Mf
    sample_dict["af"][gid] = af

In [ ]:
# Prepare the dictionary that should be fed to jinja2
jinja2_data_dict = []
for idx, event in enumerate(event_list):
    jinja2_data_dict.append({"catalog_id": event})

In [ ]:
# Compute summary statistics: median, 90% CI limits
for idx, event in enumerate(event_list):
    for param in params:
        try:
            jinja2_data_dict[idx][param+"_median"] = np.median(sample_dict[param][event])
            # 5th-percentile relative to the median
            jinja2_data_dict[idx][param+"_lower_limit"] = np.median(sample_dict[param][event]) - np.percentile(sample_dict[param][event], 5)
            # 95th-percentile relative to the median
            jinja2_data_dict[idx][param+"_upper_limit"] = np.percentile(sample_dict[param][event], 95) - np.median(sample_dict[param][event])
        except:
            # That parameter does not exist in the dict, returning np.nan
            jinja2_data_dict[idx][param+"_median"] = None
            # 5th-percentile relative to the median
            jinja2_data_dict[idx][param+"_lower_limit"] = None
            # 95th-percentile relative to the median
            jinja2_data_dict[idx][param+"_upper_limit"] = None       

In [ ]:
# IMR list

In [ ]:
event_name_list = ["GW150914", "GW170104", '\\NAME{GW190519A}','\\NAME{GW190521B}', "\\NAME{GW190630A}", \
              "\\NAME{GW190728A}", '\\NAME{GW190910A}', "\\NAME{GW191109A}", "\\NAME{GW200129A}", \
              "\\NAME{GW200208A}", "\\NAME{GW200224A}", "\\NAME{GW200311B}"]

In [ ]:
# Format the output, and show a dash for nan
for idx, event_name in enumerate(event_name_list):
    # IMR
    jinja2_data_dict[idx]["event_name"] = event_name
    try:
        jinja2_data_dict[idx]["freq_modGR"] = "${0:.1f}^{{+{1:.1f}}}_{{-{2:.1f}}}$".format(jinja2_data_dict[idx]["freq_modGR_median"], jinja2_data_dict[idx]["freq_modGR_upper_limit"], jinja2_data_dict[idx]["freq_modGR_lower_limit"])
        jinja2_data_dict[idx]["tau_modGR"] = "${0:.2f}^{{+{1:.2f}}}_{{-{2:.2f}}}$".format(jinja2_data_dict[idx]["tau_modGR_median"], jinja2_data_dict[idx]["tau_modGR_upper_limit"], jinja2_data_dict[idx]["tau_modGR_lower_limit"])
        jinja2_data_dict[idx]["Mf"] = "${0:.1f}^{{+{1:.1f}}}_{{-{2:.1f}}}$".format(jinja2_data_dict[idx]["Mf_median"], jinja2_data_dict[idx]["Mf_upper_limit"], jinja2_data_dict[idx]["Mf_lower_limit"])
        jinja2_data_dict[idx]["af"] = "${0:.2f}^{{+{1:.2f}}}_{{-{2:.2f}}}$".format(jinja2_data_dict[idx]["af_median"], jinja2_data_dict[idx]["af_upper_limit"], jinja2_data_dict[idx]["af_lower_limit"])
    except:
        jinja2_data_dict[idx]["freq_modGR"] = "$-$"
        jinja2_data_dict[idx]["tau_modGR"] = "$-$"
        jinja2_data_dict[idx]["Mf"] = "$-$"
        jinja2_data_dict[idx]["af"] = "$-$"
        
    print(f"{event_name} \t {jinja2_data_dict[idx]['freq_modGR']} \t {jinja2_data_dict[idx]['tau_modGR']} \t {jinja2_data_dict[idx]['Mf']} \t {jinja2_data_dict[idx]['af']}")

In [ ]:
# Jinja2 template for the table in LaTeX
LaTex_table_jinja_template = r"""
\begin{tabular}{lllllll}
\toprule
Event & $\fngr{220}$ (Hz) & $\taungr{220}$ (ms) & $(1+z)M_f/M_{\odot}$ & $\chi_f$ \\[0.075cm]
\midrule
\hline
{% for event in  jinja2_data_dict %}
{{ event.event_name }} &
{{ event.freq_modGR }} &
{{ event.tau_modGR }} &
{{ event.Mf }} &
{{ event.af }}
\\[0.075cm]
{% endfor %}
\bottomrule
\end{tabular}
"""